In [1]:
from __future__ import print_function

import tensorflow as tf
import numpy as np
from tensorflow.contrib import rnn

tf.set_random_seed(777)

In [2]:
sentence = ("Miracles happen to only those who believe in them. "
            "Think like a man of action and act like man of thought. "
            "Courage is very important. Like a muscle, it is strengthened by use. "
            "Life is the art of drawing sufficient conclusions from insufficient premises. "
            "By doubting we come at the truth.")

char_set = list(set(sentence)) # 유니크한 문자만 추출하기
char_dic = {w: i for i, w in enumerate(char_set)} # 각 문자들을 인덱스 형태로 나열하기

print(char_dic)

{'a': 0, ' ': 1, 't': 2, 'r': 3, 'i': 4, 'y': 5, 'e': 6, 'C': 7, 'L': 8, 'f': 9, 'l': 10, 'h': 11, 'p': 12, 'v': 13, 'u': 14, ',': 15, 'w': 16, '.': 17, 'B': 18, 'n': 19, 's': 20, 'b': 21, 'T': 22, 'M': 23, 'd': 24, 'm': 25, 'k': 26, 'c': 27, 'o': 28, 'g': 29}


In [3]:
'''
학습할 데이터를 정제합니다.
'''

data_dim = len(char_set)
hidden_size = len(char_set)
num_classes = len(char_set)
sequence_length = 10 # 임의의 길이 설정하기
learning_rate = 0.1

dataX = []
dataY = []
for i in range(0, len(sentence) - sequence_length):
    # 단어를 임의의 길이로 잘라서 연결하기
    x_str = sentence[i:i + sequence_length]
    y_str = sentence[i + 1: i + sequence_length + 1]
    print(i, x_str, '->', y_str)

    x = [char_dic[c] for c in x_str]  # x str to index
    y = [char_dic[c] for c in y_str]  # y str to index

    dataX.append(x)
    dataY.append(y)

0 Miracles h -> iracles ha
1 iracles ha -> racles hap
2 racles hap -> acles happ
3 acles happ -> cles happe
4 cles happe -> les happen
5 les happen -> es happen 
6 es happen  -> s happen t
7 s happen t ->  happen to
8  happen to -> happen to 
9 happen to  -> appen to o
10 appen to o -> ppen to on
11 ppen to on -> pen to onl
12 pen to onl -> en to only
13 en to only -> n to only 
14 n to only  ->  to only t
15  to only t -> to only th
16 to only th -> o only tho
17 o only tho ->  only thos
18  only thos -> only those
19 only those -> nly those 
20 nly those  -> ly those w
21 ly those w -> y those wh
22 y those wh ->  those who
23  those who -> those who 
24 those who  -> hose who b
25 hose who b -> ose who be
26 ose who be -> se who bel
27 se who bel -> e who beli
28 e who beli ->  who belie
29  who belie -> who believ
30 who believ -> ho believe
31 ho believe -> o believe 
32 o believe  ->  believe i
33  believe i -> believe in
34 believe in -> elieve in 
35 elieve in  -> lieve in t
36

In [4]:
batch_size = len(dataX)

X = tf.placeholder(tf.int32, [None, sequence_length])
Y = tf.placeholder(tf.int32, [None, sequence_length])

# One-hot encoding
X_one_hot = tf.one_hot(X, num_classes)
print(X_one_hot)  # check out the shape

Tensor("one_hot:0", shape=(?, 10, 30), dtype=float32)


In [5]:
# Hidden Size를 가지는 LSTM 셀 만들기
def lstm_cell():
    cell = rnn.BasicLSTMCell(hidden_size, state_is_tuple=True)
    return cell

# 셀을 다수의 층으로 쌓기 (깊게 쌓을수록 좋은 결과가 나옴)
multi_cells = rnn.MultiRNNCell([lstm_cell() for _ in range(2)], state_is_tuple=True)

# outputs: unfolding size x hidden size, state = hidden size
outputs, _states = tf.nn.dynamic_rnn(multi_cells, X_one_hot, dtype=tf.float32)

# FC layer
X_for_fc = tf.reshape(outputs, [-1, hidden_size])
outputs = tf.contrib.layers.fully_connected(X_for_fc, num_classes, activation_fn=None)

# reshape out for sequence_loss (펼치기 -> RNN의 Outputs과 동일한 형태)
outputs = tf.reshape(outputs, [batch_size, sequence_length, num_classes])

# All weights are 1 (equal weights) -> RNN 학습 이전에 해주는 과정
weights = tf.ones([batch_size, sequence_length])

sequence_loss = tf.contrib.seq2seq.sequence_loss(
    logits=outputs, targets=Y, weights=weights)
mean_loss = tf.reduce_mean(sequence_loss)
train_op = tf.train.AdamOptimizer(learning_rate=learning_rate).minimize(mean_loss)

In [6]:
'''
학습을 진행합니다.
'''

sess = tf.Session()
sess.run(tf.global_variables_initializer())

for i in range(500):
    _, l, results = sess.run(
        [train_op, mean_loss, outputs], feed_dict={X: dataX, Y: dataY})
    for j, result in enumerate(results):
        index = np.argmax(result, axis=1)
        print(i, j, ''.join([char_set[t] for t in index]), l)
        
# Let's print the last char of each result to check it works
results = sess.run(outputs, feed_dict={X: dataX})
for j, result in enumerate(results):
    index = np.argmax(result, axis=1)
    if j is 0:  # print all for the first result to make a sentence
        print(''.join([char_set[t] for t in index]), end='')
    else:
        print(char_set[index[-1]], end='')

0 0 dddddrrrdd 3.39764
0 1 idddddddde 3.39764
0 2 dssgLoieee 3.39764
0 3 yybbbiiudd 3.39764
0 4 g,Lriieddd 3.39764
0 5 hrrddddddd 3.39764
0 6 ooddeddssd 3.39764
0 7 veeeMMssdd 3.39764
0 8 diuMMsssdd 3.39764
0 9 bbggsssodd 3.39764
0 10 yssssssddd 3.39764
0 11 MMdooddddp 3.39764
0 12 Mkooddddpp 3.39764
0 13 ooiddddppp 3.39764
0 14  iiiiMippi 3.39764
0 15 ddMMMMiiid 3.39764
0 16 MMMMMpiidd 3.39764
0 17 wnwwwwdddp 3.39764
0 18 ddiiiddddp 3.39764
0 19 wwwwndddpp 3.39764
0 20  hLLdLdddd 3.39764
0 21 hrdddddddd 3.39764
0 22 dddMMMMdde 3.39764
0 23 ddMMMpddee 3.39764
0 24 Myybbooeee 3.39764
0 25 bbbbddeedd 3.39764
0 26 wwrddddddd 3.39764
0 27 vvdeeedddd 3.39764
0 28 oddddddddd 3.39764
0 29 deeMMMdddd 3.39764
0 30 eTawwnnddd 3.39764
0 31 bbwwiddddd 3.39764
0 32 wnMddddddd 3.39764
0 33 dddddddddd 3.39764
0 34 Booooddddd 3.39764
0 35 oooorrdddd 3.39764
0 36 hmrrrddddd 3.39764
0 37 iodddddddd 3.39764
0 38 orrrdddddd 3.39764
0 39 kkrddddddd 3.39764
0 40 odddddddde 3.39764
0 41 ddiiiiiiie 3.39764
0 

1 158  eeeeeeeee 3.19162
1 159  eeeeeeeee 3.19162
1 160 eeeeeeeeee 3.19162
1 161 eeeeeeeeee 3.19162
1 162 eeeeeeeeee 3.19162
1 163  eeeeeeeee 3.19162
1 164   eeeeeeee 3.19162
1 165  eeeeeeeee 3.19162
1 166 eieeeeeeei 3.19162
1 167 ieeeeeeeei 3.19162
1 168 eeeeeeeeee 3.19162
1 169 iieeeeeeei 3.19162
1 170 ieeeeeeeee 3.19162
1 171  eeeeeeeee 3.19162
1 172 eeeeeeeeee 3.19162
1 173  eeeeeeeee 3.19162
1 174  ieeeeeeee 3.19162
1 175 ieeeeeeeee 3.19162
1 176 eeeeeeeeee 3.19162
1 177 eeeeeeeeee 3.19162
1 178 ieeeeeeeee 3.19162
1 179  ieeeeeeee 3.19162
1 180 ieeeeeeeee 3.19162
1 181 eeeeeeeeee 3.19162
1 182 eeeeeeeeee 3.19162
1 183 ieeeeeeeee 3.19162
1 184 eeeeeeeeee 3.19162
1 185 eeeeeeeeee 3.19162
1 186  ieeeeeeie 3.19162
1 187 ieeeeeeiii 3.19162
1 188  eeeeeeeii 3.19162
1 189 eeeeeeeeee 3.19162
1 190 eeeeeeeeee 3.19162
1 191 iieeeeeeei 3.19162
1 192 iieeeeeeei 3.19162
1 193 ieeeeeeeei 3.19162
1 194 ieeeeeeeei 3.19162
1 195 eeeeeeeeee 3.19162
1 196 eeeeeeeeee 3.19162
1 197  eeeeeeeee 3.19162


3 6            3.09845
3 7            3.09845
3 8            3.09845
3 9            3.09845
3 10            3.09845
3 11            3.09845
3 12            3.09845
3 13            3.09845
3 14            3.09845
3 15            3.09845
3 16            3.09845
3 17            3.09845
3 18            3.09845
3 19            3.09845
3 20            3.09845
3 21            3.09845
3 22            3.09845
3 23            3.09845
3 24            3.09845
3 25            3.09845
3 26            3.09845
3 27            3.09845
3 28            3.09845
3 29            3.09845
3 30            3.09845
3 31            3.09845
3 32            3.09845
3 33            3.09845
3 34            3.09845
3 35            3.09845
3 36            3.09845
3 37            3.09845
3 38            3.09845
3 39            3.09845
3 40            3.09845
3 41            3.09845
3 42            3.09845
3 43            3.09845
3 44            3.09845
3 45            3.09845
3 46            3.09845
3 47            3.09

4 104            3.00236
4 105            3.00236
4 106            3.00236
4 107            3.00236
4 108            3.00236
4 109            3.00236
4 110            3.00236
4 111            3.00236
4 112            3.00236
4 113            3.00236
4 114            3.00236
4 115            3.00236
4 116            3.00236
4 117            3.00236
4 118            3.00236
4 119            3.00236
4 120            3.00236
4 121            3.00236
4 122            3.00236
4 123            3.00236
4 124            3.00236
4 125            3.00236
4 126            3.00236
4 127            3.00236
4 128            3.00236
4 129            3.00236
4 130            3.00236
4 131            3.00236
4 132            3.00236
4 133            3.00236
4 134            3.00236
4 135            3.00236
4 136            3.00236
4 137            3.00236
4 138            3.00236
4 139            3.00236
4 140            3.00236
4 141            3.00236
4 142            3.00236
4 143            3.00236


5 202            2.97107
5 203            2.97107
5 204            2.97107
5 205            2.97107
5 206            2.97107
5 207            2.97107
5 208            2.97107
5 209            2.97107
5 210            2.97107
5 211            2.97107
5 212            2.97107
5 213            2.97107
5 214            2.97107
5 215            2.97107
5 216            2.97107
5 217            2.97107
5 218            2.97107
5 219            2.97107
5 220            2.97107
5 221            2.97107
5 222            2.97107
5 223            2.97107
5 224            2.97107
5 225            2.97107
5 226            2.97107
5 227            2.97107
5 228            2.97107
5 229            2.97107
5 230            2.97107
5 231            2.97107
5 232            2.97107
5 233            2.97107
5 234            2.97107
5 235            2.97107
5 236            2.97107
5 237            2.97107
5 238            2.97107
5 239            2.97107
5 240            2.97107
5 241            2.97107


...

494 10 npen to on 0.267926
494 11 oen to onl 0.267926
494 12 on to only 0.267926
494 13  tto only  0.267926
494 14  oo only t 0.267926
494 15 ih only th 0.267926
494 16   only tho 0.267926
494 17 nonly thos 0.267926
494 18 ifly those 0.267926
494 19 nsy those  0.267926
494 20  y those w 0.267926
494 21 i those wh 0.267926
494 22  uhose who 0.267926
494 23 ihese who  0.267926
494 24  ese who b 0.267926
494 25 eue who be 0.267926
494 26 ne who bel 0.267926
494 27  swho beli 0.267926
494 28  aho belie 0.267926
494 29 ieo believ 0.267926
494 30 ho believe 0.267926
494 31 eubelieve  0.267926
494 32 noelieve i 0.267926
494 33 ielieve in 0.267926
494 34 elieve in  0.267926
494 35  ieve in t 0.267926
494 36 ikve in th 0.267926
494 37 nne in the 0.267926
494 38  e in them 0.267926
494 39 erin them. 0.267926
494 40  as them.  0.267926
494 41 issthem. T 0.267926
494 42 ngthem. Th 0.267926
494 43  ooem. Thi 0.267926
494 44 ihem. Thin 0.267926
494 45  en. Think 0.267926
494 46 en. Think  0.267926
4

495 152 n vtrength 0.268535
495 153  htrengthe 0.268535
495 154 aurengthen 0.268535
495 155  rengthene 0.268535
495 156  engthened 0.268535
495 157 angthened  0.268535
495 158  tthened b 0.268535
495 159   hened by 0.268535
495 160  hened by  0.268535
495 161  e ed by u 0.268535
495 162 o ed by us 0.268535
495 163  td by use 0.268535
495 164  d by use. 0.268535
495 165   by use.  0.268535
495 166  ay use. L 0.268535
495 167 ay use. Li 0.268535
495 168 e use. Lif 0.268535
495 169  dse. Life 0.268535
495 170 ase. Life  0.268535
495 171 se. Life i 0.268535
495 172    Life is 0.268535
495 173   Life is  0.268535
495 174  Life is t 0.268535
495 175 aife is th 0.268535
495 176 ife is the 0.268535
495 177 ne is the  0.268535
495 178   is the a 0.268535
495 179  as vhe ar 0.268535
495 180 as the art 0.268535
495 181 n vhe art  0.268535
495 182  hhe art o 0.268535
495 183 ahe trt of 0.268535
495 184  e art of  0.268535
495 185 o art of d 0.268535
495 186  a t of dr 0.268535
495 187 a t of dra 0

497 97 iheught. C 0.269226
497 98  eught. Co 0.269226
497 99 o ght. Cou 0.269226
497 100 nrht. Cour 0.269226
497 101 sht. Coura 0.269226
497 102  t. Courag 0.269226
497 103 o. Courage 0.269226
497 104   Lourage  0.269226
497 105  Lourage i 0.269226
497 106 iourage is 0.269226
497 107 ourage is  0.269226
497 108 nrage is v 0.269226
497 109 sage is ve 0.269226
497 110 ace is ver 0.269226
497 111 ne is very 0.269226
497 112   is very  0.269226
497 113  as very i 0.269226
497 114 is very im 0.269226
497 115 n very imp 0.269226
497 116  hery impo 0.269226
497 117 iery impor 0.269226
497 118 e y import 0.269226
497 119  y importa 0.269226
497 120 a importan 0.269226
497 121  important 0.269226
497 122 isportant. 0.269226
497 123 nportant.  0.269226
497 124 aortant. L 0.269226
497 125 rrtant. Li 0.269226
497 126 ntant. Lik 0.269226
497 127 a nt. Like 0.269226
497 128  nt. Like  0.269226
497 129 n . Like a 0.269226
497 130    Like a  0.269226
497 131   Like a m 0.269226
497 132  Life a mu 0.26

498 195  awing suf 0.26829
498 196 aging suff 0.26829
498 197 ning suffi 0.26829
498 198 ing suffic 0.26829
498 199 ng wuffici 0.26829
498 200   sufficie 0.26829
498 201  wufficien 0.26829
498 202 atfficient 0.26829
498 203  fficient  0.26829
498 204 sficient p 0.26829
498 205  icient co 0.26829
498 206  cient pon 0.26829
498 207 nient ponc 0.26829
498 208 lent poncl 0.26829
498 209 nnt ponclu 0.26829
498 210  t ponclus 0.26829
498 211   ponclusi 0.26829
498 212 hlonclusio 0.26829
498 213 aonclusion 0.26829
498 214 lnclusions 0.26829
498 215 nslusions  0.26829
498 216  lusions f 0.26829
498 217 lesions fr 0.26829
498 218 isions fro 0.26829
498 219 scons from 0.26829
498 220  ons from  0.26829
498 221 nns from i 0.26829
498 222 ns from in 0.26829
498 223  ufrom ins 0.26829
498 224  srom insu 0.26829
498 225 arom insuf 0.26829
498 226  om insuff 0.26829
498 227 am insuffi 0.26829
498 228 neinsuffic 0.26829
498 229 ainsuffici 0.26829
498 230 assufficie 0.26829
498 231 ngufficien 0.26829
4

iracles happen to only those who believe in them. Think like a man of action and act like man of thought. Courage is very important. Like a muscle, it is strengthened by use. Life is the art of drawing sufficient ponclusions from insufficient premises. By doubting we come at the truth.